In [793]:
import pandas as pd
import plotly as plt
import plotly.express as px
import plotly.graph_objs as go
from typing import Optional, List
import numpy as np
import os, math

In [794]:
MAPICONS_PATH = os.path.join("..","ressources","mapicons")

# Data prep
## Loading

In [795]:
columns = pd.read_csv("../data/_columns.csv")
bans = pd.read_csv("../data/bans.csv")
gold = pd.read_csv("../data/gold.csv")
kills = pd.read_csv("../data/kills.csv")
matchinfo = pd.read_csv("../data/matchinfo.csv")
monsters = pd.read_csv("../data/monsters.csv")
structures = pd.read_csv("../data/structures.csv")

pickban dataset, put picks along bans

In [796]:
data_dfs = [bans,gold,kills,matchinfo,monsters,structures]

It seems that LeagueofLegends already aggregates all the data, things with a list are strings though.
I think for our usecase we can simply ignore LeagueofLegends, using the separated data will be clearer.
## All
### Making ids
We should replace the "Address" with an id

In [797]:
matchinfo[matchinfo.isna().any(axis=1)]

League  Year  Season    Type blueTeamTag  bResult  rResult redTeamTag  \
3422    LMS  2015  Spring  Season         NaN        1        0        ahq   
5924    LJL  2016  Summer  Season         NaN        0        1        NaN   
5925    LJL  2016  Summer  Season         NaN        1        0        NaN   
5926    LJL  2016  Summer  Season         NaN        1        0        NaN   
5927    LJL  2016  Summer  Season         NaN        1        0        NaN   
5928    LJL  2016  Summer  Season         NaN        1        0        NaN   
5929    LJL  2016  Summer  Season         NaN        1        0        NaN   
5930    LJL  2016  Summer  Season         NaN        1        0        NaN   
5931    LJL  2016  Summer  Season         NaN        0        1        NaN   
5932    LJL  2016  Summer  Season         NaN        0        1        NaN   
5933    LJL  2016  Summer  Season         NaN        0        1        NaN   
5934    LJL  2016  Summer  Season         NaN        0        1        NaN   
5935    LJL  2016  Summer  Season         NaN        1        0        NaN   
5936    LJL  2016  Summer  Season         NaN        0        1        NaN   
5937    LJL  2016  Summer  Season         NaN        1        0        NaN   
5938    LJL  2016  Summer  Season         NaN        0        1        NaN   
5939    LJL  2016  Summer  Season         NaN        1        0        NaN   
5940    LJL  2016  Summer  Season         NaN        0        1        NaN   
5941    LJL  2016  Summer  Season         NaN        0        1        NaN   
5942    LJL  2016  Summer  Season         NaN        0        1        NaN   
5943    LJL  2016  Summer  Season         NaN        0        1        NaN   
5944    LJL  2016  Summer  Season         NaN        0        1        NaN   
5945    LJL  2016  Summer  Season         NaN        0        1        NaN   
5946    LJL  2016  Summer  Season         NaN        0        1        NaN   
5947    LJL  2016  Summer  Season         NaN        0        1        NaN   
5948    LJL  2016  Summer  Season         NaN        1        0        NaN   
5949    LJL  2016  Summer  Season         NaN        0        1        NaN   
5950    LJL  2016  Summer  Season         NaN        1        0        NaN   
5951    LJL  2016  Summer  Season         NaN        1        0        NaN   
5952    LJL  2016  Summer  Season         NaN        0        1        NaN   
5953    LJL  2016  Summer  Season         NaN        1        0        NaN   
5954    LJL  2016  Summer  Season         NaN        1        0        NaN   
5955    LJL  2016  Summer  Season         NaN        1        0        NaN   
5956    LJL  2016  Summer  Season         NaN        1        0        NaN   
5957    LJL  2016  Summer  Season         NaN        1        0        NaN   
5958    LJL  2016  Summer  Season         NaN        0        1        NaN   
5959    LJL  2016  Summer  Season         NaN        1        0        NaN   
5960    LJL  2016  Summer  Season         NaN        0        1        NaN   

      gamelength blueTop  ... redTopChamp redJungle redJungleChamp redMiddle  \
3422          32   Steak  ...      Maokai     Albis         LeeSin  westdoor   
5924          27     NaN  ...   TahmKench       NaN         Graves       NaN   
5925          41     NaN  ...        Ekko       NaN         Gragas       NaN   
5926          31     NaN  ...      Maokai       NaN         Gragas       NaN   
5927          47     NaN  ...        Ekko         =         RekSai       NaN   
5928          29     NaN  ...        Ekko       NaN         Gragas       NaN   
5929          61     NaN  ...      Maokai         =         RekSai       NaN   
5930          34     NaN  ...        Gnar       NaN         Gragas       NaN   
5931          36     NaN  ...        Ekko       NaN         Graves       NaN   
5932          33     NaN  ...     Trundle       NaN         LeeSin       NaN   
5933          42     NaN  ...        Ekko       NaN          Elise       NaN   
59

In [798]:
matchinfo = matchinfo.dropna()

In [799]:
match_ids = matchinfo["Address"].reset_index()
match_ids = match_ids.rename(columns={"index":"match_id"})

Testing code for the replacement:
```python
kills=kills.merge(match_ids, on="Address",how="left")
kills.drop(columns=["Address"],inplace=True)
```

In [800]:
for i in range(len(data_dfs)):
    data_dfs[i]=data_dfs[i].merge(match_ids, on="Address",how="inner")
    data_dfs[i].drop(columns=["Address"],inplace=True)
bans,gold,kills,matchinfo,monsters,structures = data_dfs
    

### Cardinality

In [801]:
monsters['cardinality'] = monsters.sort_values("Time").groupby("match_id").cumcount()
kills['cardinality'] = kills.sort_values("Time").groupby("match_id").cumcount()
structures['cardinality'] = structures.sort_values("Time").groupby("match_id").cumcount()

### Side

In [802]:
kills['Team'] = kills.loc[:,'Team'].apply(lambda x: 'RED' if x[0]=='r' else 'BLUE')
monsters['Team'] = monsters.loc[:,'Team'].apply(lambda x: 'RED' if x[0]=='r' else 'BLUE')
structures['Team'] = structures.loc[:,'Team'].apply(lambda x: 'RED' if (x[0]=='r' or x[0]=='R') else 'BLUE')

## Matchinfo
### Add bans

In [803]:
bans['Team'] = bans['Team'].apply(lambda x: 'red' if x[0]=='r' else 'blue')
bans = bans.rename(columns={"ban_1":"Ban1","ban_2":"Ban2","ban_3":"Ban3","ban_4":"Ban4","ban_5":"Ban5"})
bans = bans.drop_duplicates().pivot(index='match_id',columns='Team',values=["Ban1","Ban2","Ban3","Ban4","Ban5"])
bans.columns = bans.columns.map(lambda col: f"{col[1]}{col[0]}")
matchinfo = matchinfo.merge(bans,on='match_id')

### Normalize player names and team tags

In [804]:
## Team Tags fully capitalized
matchinfo['blueTeamTag'] = matchinfo['blueTeamTag'].str.upper()
matchinfo['redTeamTag'] = matchinfo['redTeamTag'].str.upper()
## Normalize player names (Some have varying capitalization)
player_cols = matchinfo.iloc[:,9::2].iloc[:,:10].columns
all_usernames = pd.Series(pd.unique(matchinfo[player_cols].values.ravel())).dropna()
most_common_variants = ( # Map lowercased usernames to their most common variant
    all_usernames.groupby(all_usernames.str.lower())
    .agg(lambda x: x.value_counts().idxmax())
    .to_dict())
for col in player_cols:
    matchinfo[col] = matchinfo[col].str.lower().map(most_common_variants) # Keep only most recurring variatnt of username

## Kills
### Position
- Change coordinates to numeric

In [805]:
kills = kills.dropna(subset=['Victim']) # On Victim, because (although unclear) victim could die from neutral entity. Assists can and may be NaN
kills = kills[kills['Killer'] != 'TooEarly'] # Special case
kills.loc[:,'x_pos'] = pd.to_numeric(kills.loc[:,'x_pos'],errors='coerce') # Convert kill positions to numbers, coerce will convert or if not possible replace with NaN
kills.loc[:,'y_pos'] = pd.to_numeric(kills.loc[:,'y_pos'],errors='coerce') # Convert kill positions to numbers, coerce will convert or if not possible replace with NaN

### Team tags & Player names

In [806]:
## Team tags
kills = kills.merge(matchinfo.reset_index()[['match_id', 'blueTeamTag', 'redTeamTag']], on='match_id', how='left') # Merge kills with team tags based on match_id
kills['Killer_Team'] = np.where(kills['Team'] == 'BLUE', kills['blueTeamTag'], kills['redTeamTag']) # Assign Killer_Team based on 'Team' column
kills['Victim_Team'] = np.where(kills['Team'] == 'BLUE', kills['redTeamTag'], kills['blueTeamTag']) # Assign Victim_Team based on 'Team' column
kills.drop(columns=['blueTeamTag', 'redTeamTag'], inplace=True)
## Player names
def extract_username(full_str, team_tag):
    if pd.isna(full_str): # Assists can be NaN. At this point no Killer/Victim/Time is NaN (verified)
        return full_str
    
    parts = full_str.split(" ")
    if len(parts) < 2:
        return full_str  # Unusual format, return as-is (team tag missing)
    if parts[0].upper() == team_tag:
        return " ".join(parts[1:]) # First part is team tag, return rest
    else:
        return full_str  # Assume already a username
cols_to_clean = ['Killer', 'Victim', 'Assist_1', 'Assist_2', 'Assist_3', 'Assist_4']
for col in cols_to_clean:
    if 'Victim' in col:
        kills[col] = kills.apply(lambda row: extract_username(row[col], row['Victim_Team']), axis=1)
    else:
        kills[col] = kills.apply(lambda row: extract_username(row[col], row['Killer_Team']), axis=1)
    kills[col] = kills[col].str.lower().map(most_common_variants) # Keep only most recurring variatnt of username

## Monsters
### Subtypes

In [807]:
monsters = monsters.dropna()
monsters.loc[:,'Subtype'] = monsters.loc[:,'Type'].apply(lambda x: x.split('_')[0] if 'DRAGON' in x and '_' in x else None)
monsters.loc[:,'Type'] = monsters.loc[:,'Type'].apply(lambda x: 'DRAGON' if 'DRAGON' in x else x)
drake_rename = {'FIRE':'INFERNAL','EARTH':'MOUNTAIN','WATER':'OCEAN','AIR':'CLOUD'}
monsters.loc[:,'Subtype'] = monsters['Subtype'].apply(lambda x: drake_rename[x] if x in drake_rename.keys() else x)
monsters['type_cardinality'] = monsters.sort_values("Time").groupby(["match_id","Type"]).cumcount().astype(int)

In [808]:
## Lane/Type
structures = structures.dropna()
structures.loc[:,'Lane'] = structures.loc[:,'Lane'].apply(lambda x: x.split('_')[0])
structures.loc[:,'Type'] = structures.loc[:,'Type'].apply(lambda x: x.split('_')[0])
structures['type_cardinality'] = structures.sort_values("Time").groupby(["match_id","Type"]).cumcount().astype(int) # Specific for Nexus Tower assignation countW
# Boolean mask where Type is "NEXUS"
nexus_mask = structures['Type'] == 'NEXUS'
# Set 'Lane' to "UPPER" or "LOWER" based on even/odd type_cardinality
structures.loc[nexus_mask, 'Lane'] = np.where(
    structures.loc[nexus_mask, 'type_cardinality'] % 2 == 0,
    'UPPER',
    'LOWER'
)

C:\Users\Loïc\AppData\Local\Temp\ipykernel_30508\1939630904.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Structures
### Lane & Type


# Plots
## Kills


In [809]:
def add_map_bg(fig):
    #fig.update_traces(opacity=0.66)
    fig.update_layout(
        images=[
            dict(
                source="..\\ressources\\SummonersRift.webp",  # Path or URL to the PNG/SVG image
                xref="paper",  # Coordinates system: 'paper' means relative to the paper's area
                yref="paper",
                x=0,  # Positioning the image
                y=1,  # Positioning the image
                sizex=1,  # Image width as a fraction of plot area
                sizey=1,  # Image height as a fraction of plot area
                opacity=0.3,  # Image transparency (0 = fully transparent, 1 = fully opaque)
                layer="below"  # Ensures the image stays below the plot
            )
        ],
    )
    return fig

In [810]:
def combine_assists(row: pd.Series, assist_cols: List[str]) -> Optional[str]:
    assists = [str(row[col]) for col in assist_cols if pd.notna(row[col])]
    return ", ".join(assists) if assists else None

def format_time(minutes: float) -> str:
    total_seconds = int(minutes * 60)
    h = total_seconds // 3600
    m = (total_seconds % 3600) // 60
    s = total_seconds % 60
    if h > 0:
        return f"{h:02}:{m:02}:{s:02}"
    else:
        return f"{m}:{s:02}"

In [811]:
def get_kill_plot_single(df: pd.DataFrame) -> go.Figure:
    assist_columns = ["Assist_1", "Assist_2", "Assist_3", "Assist_4"]
    df['hover_labels'] = [f"<b>{row['Victim']}</b><br>By: {row['Killer']}<br>Assisted by: {combine_assists(row, assist_columns)}<br>At: {format_time(row['Time'])}" for _, row in df.iterrows()]
    red_team = np.where(df['Team']=="BLUE",df['Victim_Team'],df['Killer_Team'])[0] # Data being "kills", Team colour relates to killer team. More intuitive for user to have the victim's colour -> "A blue player died there"
    blue_team = np.where(df['Team']=="RED",df['Victim_Team'],df['Killer_Team'])[0]
    fig = px.scatter(
        data_frame=df,
        x=df['x_pos'],
        y=df['y_pos'],
        title="Deaths",
        width=800,
        height=800,
        color='Victim_Team',
        color_discrete_map={blue_team:'blue',red_team:'red'},
        labels={'Victim_Team':'Team'},
        custom_data=['hover_labels'],  # Pass hover_labels as custom_data
    )
    fig.update_traces(
        marker=dict(size=15),
        hovertemplate="%{customdata[0]}<extra></extra>"  # Use only the value from custom_data
        )
    df.drop(columns=['hover_labels'],inplace=True)
    return fig

def get_kill_plot_aggregate(df: pd.DataFrame, heatmap_binsize: int) -> go.Figure:
    df_div = df.copy()
    df_div['x_pos'] = (df_div['x_pos']/df['x_pos'].max()*heatmap_binsize).apply(math.floor)
    df_div['y_pos'] = (df_div['y_pos']/df['y_pos'].max()*heatmap_binsize).apply(math.floor)
    df_div = df_div.groupby(['x_pos', 'y_pos', 'Team']).agg(count=('Time', 'count'),avg_time=('Time', 'mean')).reset_index()
    df_div['Team'] = np.where(df_div['Team'] == 'BLUE', "Red Side", " Blue Side")
    df_div['hover_labels'] = [f"<b>Count: {row['count']}</b><br>At: {format_time(row['avg_time'])}" for _, row in df_div.iterrows()]
    fig = px.scatter(
        data_frame=df_div,
        y=df_div['y_pos'],
        x=df_div['x_pos'],
        title="Deaths",
        width=800,
        height=800,
        color='Team',
        #color_discrete_map={'RED':'blue','BLUE':'red'},
        size='count',
        custom_data=['hover_labels'],  # Pass hover_labels as custom_data
    )
    fig.update_traces(
        hovertemplate="%{customdata[0]}<extra></extra>"  # Use only the value from custom_data
        )
    return fig

def get_kill_plot(df: pd.DataFrame, heatmap_binsize: int = 25) -> go.Figure:
    if df['match_id'].unique().size == 1: fig = get_kill_plot_single(df)
    else: fig = get_kill_plot_aggregate(df, heatmap_binsize)
    add_map_bg(fig)
    return fig

In [812]:

heatmap_binsize = 25

In [813]:
fix_g=kills[kills['match_id']==7619]
fig = get_kill_plot(fix_g)
# Add timeframe
fig.show()

C:\Users\Loïc\AppData\Local\Temp\ipykernel_30508\2631682658.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\Loïc\AppData\Local\Temp\ipykernel_30508\2631682658.py:22: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [814]:
fig = get_kill_plot(kills,33)
# Add timeframe
fig.show()

In [815]:
def get_kill_heatmap(df: pd.DataFrame, heatmap_binsize: int):
    fig=px.density_heatmap(
        x=df['x_pos'],
        y=df['y_pos'],
        nbinsx=heatmap_binsize, # Define "size" of blocks
        nbinsy=heatmap_binsize,
        title="Kills",
        width=800,
        height=800,
        color_continuous_scale='Viridis'
        )
    add_map_bg(fig)
    return fig


### Turret positions (x,y)
Red Top 1 - (1000,10000)
Red Top 2 - (1600, 6200)
Red Top 3 - (1200, 4000)
Red Top inhib - (1100, 3500)
Red Mid 1 - (5800, 6000)
Red Mid 2 - (5200,4300)
Red Mid 3 - (3700, 3200)
Red Mid inhib - (3300,3200)
Red Bot 1 - (10500, 700)
Red Bot 2 - (6800, 1500)
Red Bot 3 - (4200,1200)
Red Bot inhib - (3400,1200)
Red Nexus 1 - (1700,2200)
Red Nexus 2 - (2100, 1700)

In [816]:
heatmap_binsize = 100

In [817]:
fig = get_kill_heatmap(kills,heatmap_binsize)
fig.show()

```python
fig.update_layout(
    yaxis=dict(scaleanchor="x")  # Locks x and y scaling
) 
```
This would lock x and y to equal scaling.

Summoners' Rift image from: https://www.reddit.com/r/leagueoflegends/comments/pl92ho/vector_map_of_summoners_rift_wip/

Things to filter by: blue team, red team, team name, player, by minute N, between minutes N and T.

Scatterplot version for single games.
## Monsters

We have elemental drakes. I suggest adding a column to check if it's a drake at all and one to check if it's a first drake, soul etc...
I would do a distribution of red/blue time for who takes first drake/herald/baron, as well as one giving the average time at which the first drake is taken, depending on its type.

In [818]:
# Average timestamp for killing first drake per element
#monsters.loc[monsters.groupby(['match_id','Type'])['Time'].idxmin()].groupby(['Subtype','Team']).aggregate({'Time':'mean'})
time_monst=monsters.loc[monsters.groupby(['match_id','Type'])['Time'].idxmin()].groupby(['Subtype']).aggregate({'Time':'mean'}).sort_values('Time').reset_index()
time_monst_cols = {'INFERNAL':'red','OCEAN':'blue','CLOUD':'yellow','MOUNTAIN':'green'}


In [819]:
time_monst

Subtype       Time
0  INFERNAL  10.610924
1     OCEAN  12.125621
2  MOUNTAIN  13.045458
3     CLOUD  14.459662

In [820]:
import base64

def encode_image_to_base64(path):
    with open(path, 'rb') as f:
        image_bytes = f.read()
    encoded = base64.b64encode(image_bytes).decode()
    return f'data:image/png;base64,{encoded}'

In [821]:
def get_first_Drake_avg(monsters: pd.DataFrame) -> go.Figure:
    time_monst=monsters.loc[monsters.groupby(['match_id','Type'])['Time'].idxmin()].groupby(['Subtype']).aggregate({'Time':'mean'}).sort_values('Time').reset_index()
    time_monst_cols = {'INFERNAL':'red','OCEAN':'blue','CLOUD':'yellow','MOUNTAIN':'green','ELDER':'cyan'} 
    fig=px.bar(time_monst,
            x="Subtype",
            y="Time",
            color="Subtype",
            width=500,
            color_discrete_map=time_monst_cols)
    # Rename y-axis
    fig.update_traces(width=0.85)\
        .update_xaxes(showticklabels=False)\
        .update_layout(showlegend=False,
                       yaxis_title='Average time for first clear',)
    # Add icons to graph
    for elem in time_monst['Subtype']:
        fig.add_layout_image(
            # Could do encorde for all in advance and cache
            source=encode_image_to_base64(f"{os.path.join(MAPICONS_PATH,elem)}.png"),
            x=elem,
            y=0.05,  # Right at x-axis
            xref="x",
            yref="paper",
            sizex=0.5,
            sizey=0.1,
            xanchor="center",
            yanchor="top",
            layer="above"
        )
    return fig

In [822]:
fig = get_first_Drake_avg(monsters)
fig.show()

In [823]:
fix_m = monsters[monsters['match_id']==7619].sort_values('Time')
fig = get_first_Drake_avg(fix_m)
fig.show()

In [824]:
monsters.loc[monsters.groupby(['match_id','Type'])['Time'].idxmin()].groupby(['Type','Team']).aggregate({'Time':'mean'})

Time
Type         Team           
BARON_NASHOR BLUE  27.700313
             RED   27.468074
DRAGON       BLUE  12.299946
             RED   12.076242
RIFT_HERALD  BLUE  14.528584
             RED   14.399946

In [825]:
monsters[monsters['match_id']==7619].sort_values(['Time'])

Team    Time          Type  match_id  cardinality   Subtype  \
22031  BLUE  16.195   RIFT_HERALD      7619            0      None   
36600   RED  16.217        DRAGON      7619            1  MOUNTAIN   
14063  BLUE  22.787        DRAGON      7619            2  INFERNAL   
42140   RED  26.427  BARON_NASHOR      7619            3      None   
36599   RED  29.624        DRAGON      7619            4     CLOUD   
42141   RED  35.277  BARON_NASHOR      7619            5      None   
36598   RED  35.963        DRAGON      7619            6     ELDER   

       type_cardinality  
22031                 0  
36600                 0  
14063                 1  
42140                 0  
36599                 2  
42141                 1  
36598                 3

In [826]:
monsters.groupby(['cardinality', 'Type']).aggregate(count=('Type','size'),avg_time=('Time','mean')).reset_index()

cardinality          Type  count   avg_time
0             0  BARON_NASHOR     20  26.401100
1             0        DRAGON   6549  11.702060
2             0   RIFT_HERALD   1013  12.066207
3             1  BARON_NASHOR    275  24.099262
4             1        DRAGON   5112  17.707411
5             1   RIFT_HERALD   2179  14.731605
6             2  BARON_NASHOR   1490  24.980634
7             2        DRAGON   5065  21.877218
8             2   RIFT_HERALD    880  16.988633
9             3  BARON_NASHOR   2832  26.952337
10            3        DRAGON   3896  25.944970
11            3   RIFT_HERALD    190  17.485895
12            4  BARON_NASHOR   2355  30.243897
13            4        DRAGON   3219  29.721784
14            4   RIFT_HERALD     79  18.296456
15            5  BARON_NASHOR   1694  34.329555
16            5        DRAGON   2213  33.083393
17            5   RIFT_HERALD      3  19.393667
18            6  BARON_NASHOR   1160  37.075603
19            6        DRAGON   1259  37.087576
20            7  BARON_NASHOR    594  41.298754
21            7        DRAGON    708  39.874302
22            8  BARON_NASHOR    327  45.165024
23            8        DRAGON    320  43.898297
24            9  BARON_NASHOR    149  48.243067
25            9        DRAGON    160  49.443044
26           10  BARON_NASHOR     80  53.425262
27           10        DRAGON     71  51.398761
28           11  BARON_NASHOR     31  56.244677
29           11        DRAGON     37  56.796270
30           12  BARON_NASHOR     17  60.385000
31           12        DRAGON     10  60.846400
32           13  BARON_NASHOR      6  65.879500
33           13        DRAGON      6  63.527000
34           14  BARON_NASHOR      5  68.293000
35           14        DRAGON      3  68.909000
36           15  BARON_NASHOR      1  77.290000
37           15        DRAGON      2  70.799000
38           16  BARON_NASHOR      1  78.340000
39           16        DRAGON      2  77.247500
40           17  BARON_NASHOR      2  79.786000
41           18        DRAGON      1  92.180000
42           19  BARON_NASHOR      1  92.364000

## Monster avg time type distribution

In [827]:
def get_objective_distribution(monsters: pd.DataFrame, normalized: bool=True) -> go.Figure:
    # Count monsters by type for each cardinality
    grouped_counts = monsters.groupby(['cardinality', 'Type']).aggregate(count=('Type','size'),avg_time=('Time','mean')).reset_index()
    grouped_counts['avg_time_str'] = grouped_counts['avg_time'].apply(format_time)
    if normalized:
        grouped_counts['percent'] = grouped_counts['count'] / grouped_counts.groupby('cardinality')['count'].transform('sum')
        grouped_counts['percent_str'] = (grouped_counts['percent'] * 100).map("{:.2f}%".format)
        labels = {'cardinality': 'Cardinality', 'percent_str': 'Percentage', 'count':'Count', 'avg_time_str':'Average Time'}
        hover_data={'cardinality': True, 'percent':False, 'percent_str': True, 'count': True, 'Type': True, 'avg_time_str':True}
        y='percent'
    else:
        labels = {'cardinality': 'Cardinality', 'count': 'Count', 'avg_time_str':'Average Time'}
        hover_data={'cardinality': True, 'Type': True, 'count': True, 'avg_time_str':True}
        y='count'

    fig = px.bar(
        grouped_counts,
        x='cardinality',
        y=y,
        color='Type',
        title='Distribution of Types by Cardinality',
        labels=labels,
        hover_data=hover_data,
        barmode='stack'
    )
    return fig

In [828]:
import colorsys

def hex_to_rgb(hex_color):
    """Convert hex color to RGB tuple (0–1 scale)."""
    hex_color = hex_color.lstrip("#")
    return tuple(int(hex_color[i:i+2], 16)/255.0 for i in (0, 2, 4))

def rgb_to_hex(rgb):
    """Convert RGB tuple (0–1 scale) to hex color."""
    return '#{:02x}{:02x}{:02x}'.format(
        int(rgb[0]*255), int(rgb[1]*255), int(rgb[2]*255)
    )

def generate_shades_plotly(hex_color, n_shades=3):
    """Generate n_shades of a hex color using HSV value scaling."""
    r, g, b = hex_to_rgb(hex_color)
    h, s, v = colorsys.rgb_to_hsv(r, g, b)

    value_steps = [0.5, 0.7, 0.9][:n_shades]  # Brightness levels
    shades = [colorsys.hsv_to_rgb(h, s, val) for val in value_steps]

    return [rgb_to_hex(rgb) for rgb in shades]


In [829]:
def get_struct_distribution(structures: pd.DataFrame, normalized: bool=True) -> go.Figure:
    # Count monsters by type for each cardinality
    # Define your 6 base colors for each Type (can be adjusted as needed)
    base_colors = {
        'TURRET': '#1f77b4',      # Blue
        'INHIBITOR': '#d62728',   # Red
        'NEXUS': '#9467bd',       # Purple
        'BASE': '#ff7f0e',        # Orange
    }

    # List of lanes
    lanes = ['TOP', 'MID', 'BOT', 'UPPER', 'LOWER']
    # Create full mapping
    color_map = {}
    for t, base_color in base_colors.items():
        shades = generate_shades_plotly(base_color, len(lanes))
        for lane, shade in zip(lanes, shades):
            color_map[f'{t}_{lane}'] = shade

    grouped_counts = structures.groupby(['cardinality', 'Type', 'Lane']).aggregate(count=('Type','size'),avg_time=('Time','mean')).reset_index()
    grouped_counts['avg_time_str'] = grouped_counts['avg_time'].apply(format_time)
    if normalized:
        grouped_counts['percent'] = grouped_counts['count'] / grouped_counts.groupby('cardinality')['count'].transform('sum')
        grouped_counts['percent_str'] = (grouped_counts['percent'] * 100).map("{:.2f}%".format)
        labels = {'cardinality': 'Cardinality', 'percent_str': 'Percentage', 'count':'Count', 'avg_time_str':'Average Time'}
        hover_data={'cardinality': True, 'percent':False, 'percent_str': True, 'count': True, 'Type': True, 'avg_time_str':True}
        y='percent'
    else:
        labels = {'cardinality': 'Cardinality', 'count': 'Count', 'avg_time_str':'Average Time'}
        hover_data={'cardinality': True, 'Type': True, 'Lane': True, 'count': True, 'avg_time_str':True}
        y='count'

    grouped_counts['Type_Lane'] = grouped_counts['Type'] + '_' + grouped_counts['Lane']
    fig = px.bar(
        grouped_counts,
        x='cardinality',
        y=y,
        color='Type_Lane',
        title='Distribution of Types by Cardinality',
        labels=labels,
        hover_data=hover_data,
        barmode='stack'
    )
    return fig

In [830]:
get_struct_distribution(structures, False).show()

In [831]:
get_struct_distribution(fix_s, False).show()

In [832]:
get_objective_distribution(monsters, False).show()

In [833]:
get_objective_distribution(fix_m)

## Timeline:
A timeline over time. For individual games inspired from spectator one. Bar with event related icon at referred minute.
For sets of games or general view use average time for event N. Note that for aggregate views events would be drake_0, drake_1, ... same for baron and turrets.

Click on it to make it on multiple lines and have the data less condensed.

For the agglomeration, add cardinality of item in each individual dataset.
Build "Events" dataset taking only the event identification + game_id + cardinality + timestamp from these datasets.

In [834]:
def set_timeline_margins_scale(fig: go.Figure, x_size: int, y_range: list[int], y_tickvals: list[int]):
    fig.update_layout(
        xaxis=dict(
            range=[0, x_size],  # pad the view: game time
            showline=False,
            showticklabels=True,
            tickmode='auto',
        ),
        yaxis=dict(
            range=y_range,  # pad the view: consider icon size
            visible=True,
            showline=True,
            showticklabels=False,
            tickvals=y_tickvals,   # To put horizontal lines at level of icons
        ),
        margin=dict(t=40, b=40), # TODO: DETERMINED BY DASH?
        height=200, # TODO: DETERMINED BY DASH?
    )

In [835]:
def create_kills_timeline(df: pd.DataFrame, hover_labels: List[str]) -> go.Figure:
    """ Creates a timeline using df's data, df needs columns: 'count', 'Time' and 'icon_name'.
    Labels to show when hovering given separately.
    """
    
    x_size = df['Time'].max() + 1
    df.loc[:,'hover_labels'] = hover_labels
    fig = px.scatter(
            data_frame=df,
            x='Time',
            y=np.ones(df.shape[0]),
            color='Team',
            size='count',
            custom_data=['hover_labels'],  # Pass hover_labels as custom_data
    )
    fig.update_traces(
        marker=dict(sizemin=6), # Else there are many we don't see in aggregate
        hovertemplate="%{customdata[0]}<extra></extra>"  # Use only the value from custom_data
        )
    set_timeline_margins_scale(fig, x_size, [0,2], np.ones(df.shape[0]))
    return fig

def get_kills_timeline(df: pd.DataFrame) -> go.Figure:
    """ Creates a timeline of killed neutral objectives over time. 
    Should receive the data for a single match, or aggregated data"""
    # Team column is killer team
    if df['match_id'].unique().size > 1:
        # Do not consider Subtype in aggregate, because too much detail
        g_df = df.groupby(['cardinality','Team']).aggregate(count=('Team','count'),Time=('Time','mean')).sort_values('Time').reset_index()
        hover_labels = [f"Count: {row['count']}<br>At: {format_time(row['Time'])}<br>Cardinality: {row['cardinality']}" for _, row in g_df.iterrows()]
    else: 
        g_df = df
        g_df.loc[:,'count'] = 1
        assist_columns = ["Assist_1", "Assist_2", "Assist_3", "Assist_4"]
        hover_labels = [f"<b>{row['Victim']}</b><br>By: {row['Killer']}<br>Assisted by: {combine_assists(row, assist_columns)}<br>At: {format_time(row['Time'])}" for _, row in df.iterrows()]
    return create_kills_timeline(g_df, hover_labels)

In [836]:
fig = get_kills_timeline(kills)
fig.show()

In [837]:
fig = get_kills_timeline(fix_g)
fig.show()

C:\Users\Loïc\AppData\Local\Temp\ipykernel_30508\1525720383.py:33: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\Loïc\AppData\Local\Temp\ipykernel_30508\1525720383.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [838]:
kills.groupby(['cardinality','Team']).aggregate(Count=('Team','count'),Time=('Time','mean')).sort_values('Time').reset_index()

cardinality  Team  Count       Time
0              0  BLUE   3829   6.534978
1              0   RED   3632   6.638537
2              1   RED   3714   9.160124
3              1  BLUE   3861   9.284390
4              2  BLUE   3923  11.331797
..           ...   ...    ...        ...
190           64   RED      5  47.313400
191           60   RED     12  49.000917
192           65   RED      5  50.653400
193           63   RED      7  51.255571
194           67   RED      3  52.205333

[195 rows x 4 columns]

In [839]:
def create_timeline(df: pd.DataFrame, hover_labels: List[str]) -> go.Figure:
    """ Creates a timeline using df's data, df needs columns: 'count', 'Time' and 'icon_name'.
    Labels to show when hovering given separately.
    """
    fig = go.Figure()
    
    x_size = df['Time'].max() + 1
    
    tot_count = df['count'].sum()
    df['size'] = x_size/100+10*(df['count']/tot_count)  # Base size related with x axis and scales with proportion
    max_s_icon = df['size'].max()

    # x_tol defines when a neighbouring icon is to be offset by y_step. Both in funciton of icon size
    x_tol = max_s_icon*0.15
    y_step = max_s_icon

    y_values = []
    previous_x = -100
    previous_y = y_step
    # Add one image per event
    for _, row in df.iterrows():    # Add icons to plot
        img_path = f'../ressources/mapicons/{row['icon_name']}.png'
        x = row['Time']
        if x-(previous_x+x_tol) < 0: y = previous_y+y_step
        else: y = y_step
        if os.path.exists(img_path):
            fig.add_layout_image(
                source=encode_image_to_base64(img_path),
                x=x,
                y=y,
                xref="x",
                yref="y",
                sizex=row['size'],
                sizey=row['size'],
                xanchor="center",
                yanchor="middle",
                layer="above"
            )
        else: # TODO: EXCEPTION HANDLING? 
            print(f"Image not found: {img_path}")
        # Keep track of y positioning
        previous_x = x
        previous_y = y
        y_values.append(y)
    fig.add_trace(go.Scatter(   # Add invisible scatter at icon spots (for the hoverinfo)
                x=df['Time'],
                y=y_values,
                mode='markers',
                marker=dict(size=df['size'], color='rgba(0,0,0,0)'),  # invisible
                hoverinfo='text',
                text=hover_labels,
                showlegend=False
            ))
    set_timeline_margins_scale(fig, x_size, [0, max(y_values)+max_s_icon], np.unique(y_values))
    return fig

def get_monsters_timeline(df: pd.DataFrame) -> go.Figure:
    """ Creates a timeline of killed neutral objectives over time. 
    Should receive the data for a single match, or aggregated data"""
    # Team column is killer team
    if df['match_id'].unique().size > 1:
        # Do not consider Subtype in aggregate, because too much detail
        g_df = df.groupby(['Type','type_cardinality','Team']).aggregate(count=('Type','size'),Time=('Time','mean')).sort_values('Time').reset_index()
        g_df['icon_name'] = g_df['Team'] + '_' + g_df['Type']
        hover_labels = [f"<b>{" ".join(row['Type'].split('_')).title()}</b><br>At: {format_time(row['Time'])}<br>Count: {row['count']}" for _, row in g_df.iterrows()]
    else: 
        g_df = df
        g_df['count'] = 1
        g_df['icon_name'] = df['Team'] + '_' + np.where(df['Subtype'].notna(), df['Subtype'], df['Type'])
        hover_labels = [f"<b>{row['Subtype'].title()+" " if row['Subtype'] is not None else ""}{" ".join(row['Type'].split('_')).title()}</b><br>At: {format_time(row['Time'])}" for _, row in g_df.iterrows()]
    return create_timeline(g_df, hover_labels)

def get_structures_timeline(df: pd.DataFrame) -> go.Figure:
    """ Creates a timeline of destroyed structures over time. 
    Should receive the data for a single match, or aggregated data"""
    df['Time'].astype(float,False)
    g_df = df.groupby(['Type','Lane','Team']).aggregate(count=('Type','size'),Time=('Time','mean')).sort_values('Time').reset_index()
    # Team column is destroyer team -> destroyed (Blue turret destroyed)    
    g_df['icon_name'] = g_df['Team'].replace({'BLUE': 'RED', 'RED': 'BLUE'}) + '_' + np.where(g_df['Type'] == 'INHIBITOR', 'INHIBITOR', 'TURRET')
    hover_labels = [f"<b>{row['Lane'].title()} {f"{row['Type'].title()} Turret" if row['Type']!="INHIBITOR" else row['Type'].title()}</b><br>At: {format_time(row['Time'])}{"<br>Count: "+str(row['count']) if df['match_id'].unique().size > 1 else ""}" for _, row in g_df.iterrows()]
    return create_timeline(g_df, hover_labels)

In [840]:
fix_m = monsters[monsters['match_id']==7619].sort_values('Time')
fix_s = structures[structures['match_id']==7619].sort_values('Time')

In [841]:
get_monsters_timeline(fix_m).show()

In [842]:
get_monsters_timeline(monsters).show()

In [843]:
get_structures_timeline(fix_s).show()

In [844]:
get_structures_timeline(structures).show()

## Win Rate by side

In [845]:
matchinfo

League  Year  Season    Type blueTeamTag  bResult  rResult redTeamTag  \
0     NALCS  2015  Spring  Season         TSM        1        0         C9   
1     NALCS  2015  Spring  Season         CST        0        1        DIG   
2     NALCS  2015  Spring  Season         WFX        1        0         GV   
3     NALCS  2015  Spring  Season         TIP        0        1         TL   
4     NALCS  2015  Spring  Season         CLG        1        0         T8   
...     ...   ...     ...     ...         ...      ...      ...        ...   
7577    TCL  2018  Spring  Season          YC        0        1        SUP   
7578    TCL  2018  Spring  Season         GAL        0        1         DP   
7579    OPL  2018  Spring  Season         SIN        0        1         DW   
7580    OPL  2018  Spring  Season         LGC        1        0        TTC   
7581    OPL  2018  Spring  Season         TTC        0        1        LGC   

      gamelength   blueTop  ...   blueBan1   redBan1   blueBan2  redBan2  \
0             40     Dyrus  ...     Rumble  Tristana   Kassadin  Leblanc   
1             38      Cris  ...   Kassadin    RekSai      Sivir    Janna   
2             40   Flaresz  ...   JarvanIV   Leblanc  Lissandra      Zed   
3             41      Rhux  ...      Annie    RekSai  Lissandra   Rumble   
4             35     Benny  ...     Irelia    Rumble   Pantheon    Sivir   
...          ...       ...  ...        ...       ...        ...      ...   
7577          34    Elwind  ...     Ezreal      Ornn    Sejuani  Kalista   
7578          39      Rare  ...  Gangplank       Zoe    Sejuani   KogMaw   
7579          24  Praedyth  ...  TahmKench      Azir     KogMaw  Kalista   
7580          35     Ceres  ...     KogMaw   Kalista     Illaoi    Galio   
7581          42   Papryze  ...    Kalista    KogMaw       Gnar   Illaoi   

       blueBan3   redBan3    blueBan4  redBan4 blueBan5  redBan5  
0     Lissandra   Nidalee         NaN      NaN      NaN      NaN  
1     Lissandra   Leblanc         NaN      NaN      NaN      NaN  
2      Kassadin    RekSai         NaN      NaN      NaN      NaN  
3      Kassadin    LeeSin         NaN      NaN      NaN      NaN  
4      Kassadin    Rengar         NaN      NaN      NaN      NaN  
...         ...       ...         ...      ...      ...      ...  
7577       Azir      Ryze  Cassiopeia  Alistar    Corki     Shen  
7578       Azir  JarvanIV        Gnar     Ornn      Zac   Rengar  
7579       Shen     Braum     Sejuani   Maokai  Shyvana  Alistar  
7580      Urgot      Gnar      Xerath    Jayce    Karma  Sejuani  
7581       Ryze      Azir     Orianna    Karma    Sivir  Sejuani  

[7582 rows x 40 columns]

In [847]:
from plotly.subplots import make_subplots

In [906]:
def set_timeline_margins_scale(fig: go.Figure, x_size: int):
    xaxis_common = {
        "range": [0, x_size],
        "showline": False,
        "showticklabels": True,
        "tickmode": "auto",
        "col": 1,  # all xaxes are in column 1
        "matches":'x2'
    }
    for row in range(2, 5):
        fig.update_xaxes(row=row, **xaxis_common)
    fig.update_layout(
        margin=dict(l=60, r=60, t=50, b=50), # TODO: DETERMINED BY DASH?
        height=1500, # TODO: DETERMINED BY DASH?
        plot_bgcolor='rgba(0,0,0,0)',  # transparent background for all plots
    )


In [992]:
# TODO: Might have to give 'x_size' in function of highest Time value of any timeline data
def create_timeline(df: pd.DataFrame, hover_labels: List[str], x_size: int, xyref_nb: str = "") -> go.Figure:
    """ Creates a timeline using df's data, df needs columns: 'count', 'Time' and 'icon_name'.
    Labels to show when hovering given separately.
    """
    fig = go.Figure()
    
    tot_count = df['count'].sum()
    df['size'] = x_size/100+10*(df['count']/tot_count)  # Base size related with x axis and scales with proportion
    max_s_icon = df['size'].max()

    # x_tol defines when a neighbouring icon is to be offset by y_step. Both in funciton of icon size
    x_tol = max_s_icon*0.15
    y_step = max_s_icon

    y_values = []
    previous_x = -100
    previous_y = y_step

    layout_images = []
    # Add one image per event
    for _, row in df.iterrows():
        img_path = f'../ressources/mapicons/{row['icon_name']}.png'
        x = row['Time']
        if x-(previous_x+x_tol) < 0: y = previous_y+y_step
        else: y = y_step
        if os.path.exists(img_path):
            layout_images.append(dict(
                source=encode_image_to_base64(img_path),
                x=x,
                y=y,
                xref="x"+xyref_nb,
                yref="y"+xyref_nb,
                sizex=row['size'],
                sizey=row['size'],
                xanchor="center",
                yanchor="middle",
                layer="above"
            ))
        else: # TODO: EXCEPTION HANDLING? 
            print(f"Image not found: {img_path}")
        # Keep track of y positioning
        previous_x = x
        previous_y = y
        y_values.append(y)
    fig.add_trace(go.Scatter(
                x=df['Time'],
                y=y_values,
                mode='markers',
                marker=dict(size=df['size'], color='rgba(0,0,0,0)'),  # invisible
                hoverinfo='text',
                text=hover_labels,
                showlegend=False
            ))
    #set_timeline_margins_scale(fig, x_size, [0, max(y_values)+max_s_icon], np.unique(y_values))
    return fig, np.unique(y_values), max(y_values)+max_s_icon, layout_images

def get_monsters_timeline(df: pd.DataFrame, x_size: int) -> go.Figure:
    """ Creates a timeline of killed neutral objectives over time. 
    Should receive the data for a single match, or aggregated data"""
    # Team column is killer team
    if df['match_id'].unique().size > 1:
        # Do not consider Subtype in aggregate, because too much detail
        g_df = df.groupby(['Type','type_cardinality','Team']).aggregate(count=('Type','size'),Time=('Time','mean')).sort_values('Time').reset_index()
        g_df.loc[:,'icon_name'] = g_df['Team'] + '_' + g_df['Type'] # TODO: Do in preprocessing?
        hover_labels = [f"<b>{row['Type']}</b><br>At: {format_time(row['Time'])}<br>Count: {row['count']}" for _, row in g_df.iterrows()]
    else: 
        g_df = df.copy()
        g_df.loc[:,'count'] = 1
        g_df.loc[:,'icon_name'] = df['Team'] + '_' + np.where(df['Subtype'].notna(), df['Subtype'], df['Type']) # TODO: Do in preprocessing?
        hover_labels = [f"<b>{row['Type']}</b><br>At: {format_time(row['Time'])}" for _, row in g_df.iterrows()]
    return create_timeline(g_df, hover_labels, x_size, "3")

def get_structures_timeline(df: pd.DataFrame, x_size: int) -> go.Figure:
    """ Creates a timeline of destroyed structures over time. 
    Should receive the data for a single match, or aggregated data"""
    df['Time'].astype(float,False)
    g_df = df.groupby(['Type','Lane','Team']).aggregate(count=('Type','size'),Time=('Time','mean')).sort_values('Time').reset_index()
    # Team column is destroyer team -> destroyed (Blue turret destroyed)    
    g_df.loc[:,'icon_name'] = g_df['Team'].replace({'BLUE': 'RED', 'RED': 'BLUE'}) + '_' + np.where(g_df['Type'] == 'INHIBITOR', 'INHIBITOR', 'TURRET')
    hover_labels = [f"<b>{row['Lane']} {f"{row['Type']} Turret" if row['Type']!="INHIBITOR" else row['Type']}</b><br>At: {format_time(row['Time'])}{"<br>Count: "+str(row['count']) if df['match_id'].unique().size > 1 else ""}" for _, row in g_df.iterrows()]
    return create_timeline(g_df, hover_labels, x_size, "4")

In [993]:
def create_kills_timeline(df: pd.DataFrame, team_name_col: List[(str)], hover_labels: List[str]) -> go.Figure:
    """ Creates a timeline using df's data, df needs columns: 'count', 'Time' and 'icon_name'.
    Labels to show when hovering given separately.
    """

    fig = go.Figure()
    y_mod = 0
    max_size = df['count'].max()
    for team_name, color in team_name_col:
        team_data = df[df['Team'] == team_name]
        y_mod += 1

        fig.add_trace(
            go.Scatter(
                x=team_data['Time'],
                y=np.zeros(team_data.shape[0])+y_mod,
                mode='markers',
                name=team_name,
                legendgroup=team_name,  # Link traces with same team
                marker=dict(size=30*team_data['count']/max_size, sizemin=6,color=color),
                hoverinfo='text',
                text=hover_labels,
                showlegend=False
            )
        )

    #set_timeline_margins_scale(fig, x_size, [0,2], np.ones(df.shape[0]))
    return fig, [1,2], 3

def get_kills_timeline(df: pd.DataFrame) -> go.Figure:
    """ Creates a timeline of killed neutral objectives over time. 
    Should receive the data for a single match, or aggregated data"""
    # Team column is killer team
    if df['match_id'].unique().size == 1:
        df_g = df.copy()    # To avoid warning

        assist_columns = ["Assist_1", "Assist_2", "Assist_3", "Assist_4"]
        hover_labels = [f"<b>{row['Victim']}</b><br>By: {row['Killer']}<br>Assisted by: {combine_assists(row, assist_columns)}<br>At: {format_time(row['Time'])}" for _, row in df_g.iterrows()]

        blue_team = df_g.loc[df_g['Team'] == 'BLUE', 'Killer_Team'].iloc[0] # Note, killer perspective, so BLUE means blue killer and red victim
        red_team = df_g.loc[df_g['Team'] == 'BLUE', 'Victim_Team'].iloc[0]

        df_g.loc[:,'Team'] = np.where(df_g['Team'] == 'BLUE', red_team, blue_team) # Invert color on the map, more user friendly if a dot fits the player who died
        df_g.loc[:,'count'] = 1 # Just to be consistent with the aggregated version and have a "count" column for the size
        team_name_col=[(red_team,'red'),(blue_team,'blue')]
    else: 
        # Do not consider Subtype in aggregate, because too much detail
        df_g = df.groupby(['cardinality','Team']).aggregate(count=('Team','count'),Time=('Time','mean')).sort_values('Time').reset_index()
        hover_labels = [f"Count: {row['count']}<br>At: {format_time(row['Time'])}<br>Cardinality: {row['cardinality']}" for _, row in df_g.iterrows()]
        df_g.loc[:,'Team'] = np.where(df_g['Team'] == 'BLUE', "Red Side", "Blue Side")
        team_name_col=[("Red Side", "red"), ("Blue Side", "blue")]
    return create_kills_timeline(df_g, team_name_col, hover_labels)

In [994]:
def create_kill_plot(df_g: pd.DataFrame, team_name_col: List[(str)], hover_labels: List[str], coord_suffix: str) -> go.Figure:
    max_size = df_g['count'].max()
    # Create figure
    fig = go.Figure()
    for team_name, color in team_name_col:
        team_data = df_g[df_g['Team'] == team_name]
        fig.add_trace(
            go.Scatter(
                x=team_data[coord_suffix+'x_pos'],
                y=team_data[coord_suffix+'y_pos'],
                mode='markers',
                name=team_name,
                legendgroup=team_name,  # Link traces with same team
                marker=dict(size=30*team_data.loc[:,'count']/max_size, color=color),
                hoverinfo='text',
                text=hover_labels,
                showlegend=True
            )
        )
    return fig


def get_kill_heatmap(df: pd.DataFrame, heatmap_binsize: int):
    fig = go.Figure()
    heatmap = go.Histogram2d(
        x=df['x_pos'],
        y=df['y_pos'],
        nbinsx=heatmap_binsize,
        nbinsy=heatmap_binsize,
        colorscale='Viridis',
        opacity=0.6,
        colorbar=dict(
            title='Kill Density',
            x=0.80,           # Move the colorbar horizontally (0=left, 1=right)
            y=0.80,           # Move it vertically (1 is top, 0 is bottom)
            len=0.5,          # Shorten it to only cover the map row
            thickness=30,     # Width of the bar
            xanchor='left'    # Anchors the x-position
    ))
    fig.add_trace(heatmap) 
    return fig

In [995]:
def get_kill_plot(df: pd.DataFrame, heatmap_binsize: int = 25) -> go.Figure:
    if df['match_id'].unique().size == 1:
        df_g = df.copy()    # To avoid warning
        coord_suffix = ""

        assist_columns = ["Assist_1", "Assist_2", "Assist_3", "Assist_4"]
        hover_labels = [f"<b>{row['Victim']}</b><br>By: {row['Killer']}<br>Assisted by: {combine_assists(row, assist_columns)}<br>At: {format_time(row['Time'])}" for _, row in df_g.iterrows()]

        blue_team = df_g.loc[df_g['Team'] == 'BLUE', 'Killer_Team'].iloc[0] # Note, killer perspective, so BLUE means blue killer and red victim
        red_team = df_g.loc[df_g['Team'] == 'BLUE', 'Victim_Team'].iloc[0]

        df_g.loc[:,'Team'] = np.where(df_g['Team'] == 'BLUE', red_team, blue_team) # Invert color on the map, more user friendly if a dot fits the player who died
        df_g.loc[:,'count'] = 1 # Just to be consistent with the aggregated version and have a "count" column for the size
        team_name_col=[(red_team,'red'),(blue_team,'blue')]
    else: 
        coord_suffix = "bin_"
        x_max = df['x_pos'].max()
        y_max = df['y_pos'].max()
        df['bin_x_pos'] = (df['x_pos']/x_max*heatmap_binsize).apply(math.floor) # Scalow down into bins
        df['bin_y_pos'] = (df['y_pos']/y_max*heatmap_binsize).apply(math.floor)

        df_g = df.groupby(['bin_x_pos', 'bin_y_pos', 'Team']).agg(count=('Time', 'count'),avg_time=('Time', 'mean')).reset_index()

        df_g['bin_x_pos'] = df_g['bin_x_pos']*(x_max / heatmap_binsize) # Rescale the coords to original size, to be consistent with scaling between single and aggregate
        df_g['bin_y_pos'] = df_g['bin_y_pos']*(y_max / heatmap_binsize)

        df_g['Team'] = np.where(df_g['Team'] == 'BLUE', "Red Side", "Blue Side")
        hover_labels = [f"<b>Count: {row['count']}</b><br>At: {format_time(row['avg_time'])}" for _, row in df_g.iterrows()]
        team_name_col=[("Red Side", "red"), ("Blue Side", "blue")]
    return create_kill_plot(df_g, team_name_col, hover_labels, coord_suffix)

In [996]:
def get_map_bg(xref: str="paper", yref: str="paper", size: int=1) -> dict:
    """Creates a dict containing the information relating to the map background to add on the map"""
    return dict(
        source="..\\ressources\\SummonersRift.webp",  # Path or URL to the PNG/SVG image
        xref=xref,  # Coordinates system: 'paper' means relative to the paper's area
        yref=yref,
        x=0,  # Positioning the image
        y=0,  # Positioning the image
        sizex=size,  # Adjust based on your coordinate system
        sizey=size,
        xanchor="left",
        yanchor="bottom",
        sizing="stretch",  # Or "contain", "fill"
        opacity=0.3,  # Image transparency (0 = fully transparent, 1 = fully opaque)
        layer="below"  # Ensures the image stays below the plot
    )

In [997]:
def get_map_timeline_mplot(dfkills, dfmons, dfstruct):
    # get timeframe filter and apply
    # time_filtered_kills = filtered_kills.applytimefilter
    # get whether heatmap or scatter
    heatmap = False
    # get binsize from selector
    binsize = 50

    # Fix preliminary values
    map_size = 14650 # This is how it is
    row_h = [0.6,0.13,0.13,0.14]

    # Compute xaxis size based on my gamelength of !filtered! data
    x_size = matchinfo['gamelength'].max() + 1

    # Create the traces
    if heatmap:
        fig1 = get_kill_heatmap(dfkills, binsize)   # recommend 100 (50 OK), else ugly
    else:
        fig1 = get_kill_plot(dfkills, binsize)  # reccommend 50 max else laggy
    fig2,fig2_yvals,fig2_y_max = get_kills_timeline(dfkills)
    fig3,fig3_yvals,fig3_y_max, fig3imgs = get_monsters_timeline(dfmons, x_size)
    fig4,fig4_yvals,fig4_y_max, fig4imgs = get_structures_timeline(dfstruct, x_size)

    # create subplots
    fig = make_subplots(
        rows=4, cols=1,
        shared_xaxes=False,
        row_heights=row_h,
        vertical_spacing=0.1,
        subplot_titles=("Map", "Kills Timeline", "Monsters Timeline", "Structures Timeline")
    )

    # Add figure 1 (map) to subplots
    for trace in fig1.data:
        fig.add_trace(trace, row=1, col=1)
    # Enforce square map (equal unit scale)
    fig1_axis_common = {"showline": False, "showticklabels": False, "row":1, "col":1, "showgrid":False}
    fig.update_yaxes(range=[0, map_size], **fig1_axis_common)
    fig.update_xaxes(range=[0, map_size], scaleanchor='y', **fig1_axis_common)
    map_bg_img = get_map_bg("x1","y1",map_size) # Dict to be added to list of images set alter

    # yaxis related settings that are fix for timelines
    timeline_axes_common = {"visible":True, "showline":True, "linecolor":'gray',"gridcolor":'gray',"showticklabels":False, "col":1, "autorange":False, "fixedrange":True}

    # Add figure 2 (kills timeline)
    for trace in fig2.data:
        fig.add_trace(trace, row=2, col=1)
    fig.update_yaxes(
        range=[0,fig2_y_max],  # pad the view: consider icon size
        tickvals=fig2_yvals,   # To put horizontal lines at level of icons
        row=2, **timeline_axes_common
    )
    # Add figure 3 (monsters timeline)
    for trace in fig3.data:
        fig.add_trace(trace, row=3, col=1)
    fig.update_yaxes(
        range=[0,fig3_y_max],  # pad the view: consider icon size
        tickvals=fig3_yvals,   # To put horizontal lines at level of icons
        row=3, **timeline_axes_common
    )
    # Add figure 4 (structures timeline)
    for trace in fig4.data:
        fig.add_trace(trace, row=4, col=1)
    fig.update_yaxes(
        range=[0,fig4_y_max],  # pad the view: consider icon size
        tickvals=fig4_yvals,   # To put horizontal lines at level of icons
        row=4, **timeline_axes_common
    )

    fig.layout.images = fig3imgs+fig4imgs+[map_bg_img]  # Add images, monster, structure icons and map bg
    set_timeline_margins_scale(fig, x_size)

    return fig

In [998]:
fix_g=kills[kills['match_id']==7619]
fix_s=structures[structures['match_id']==7619]
fix_m=monsters[monsters['match_id']==7619]
#get_map_timeline_mplot(kills, monsters, structures).show()
get_map_timeline_mplot(fix_g, fix_m, fix_s).show()

In [1021]:
gold

Type  min_1  min_2  min_3  min_4  min_5  min_6  min_7  min_8  \
0            golddiff      0      0    -14    -65   -268   -431   -488   -789   
1            golddiff      0      0    -26    -18    147    237   -152     18   
2            golddiff      0      0     10    -60     34     37    589   1064   
3            golddiff      0      0    -15     25    228     -6   -243    175   
4            golddiff     40     40     44    -36    113    158   -121   -191   
...               ...    ...    ...    ...    ...    ...    ...    ...    ...   
98561  goldredSupport    500    500    566    801   1004   1234   1463   1674   
98562  goldredSupport    500    500    587    790   1107   1335   1472   1616   
98563  goldredSupport    500    500    585    770    976   1222   1446   1627   
98564  goldredSupport    500    500    592    788   1006   1251   1490   1704   
98565  goldredSupport    500    500    585    793    998   1201   1373   1619   

       min_9  ...  min_87  min_88  min_89  min_90  min_91  min_92  min_93  \
0       -494  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1         88  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2       1258  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3       -346  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4         23  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
...      ...  ...     ...     ...     ...     ...     ...     ...     ...   
98561   1906  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
98562   1895  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
98563   1900  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
98564   1936  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
98565   1835  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

       min_94  min_95  match_id  
0         NaN     NaN         0  
1         NaN     NaN         1  
2         NaN     NaN         2  
3         NaN     NaN         3  
4         NaN     NaN         4  
...       ...     ...       ...  
98561     NaN     NaN      7615  
98562     NaN     NaN      7616  
98563     NaN     NaN      7617  
98564     NaN     NaN      7618  
98565     NaN     NaN      7619  

[98566 rows x 97 columns]

In [1002]:
wins=matchinfo.loc[:,['bResult','rResult']].sum()
d = {"WIN RATE BLUE":wins['bResult']/wins.sum()*100,"WIN RATE RED":wins['rResult']/wins.sum()*100}

In [1015]:
wins

bResult    4127
rResult    3455
dtype: int64

In [1023]:
fix_mi = matchinfo[matchinfo["match_id"] == 3333]

In [1034]:
mask = ( (cols == team_a).any(axis=1) ) & ( (cols == team_b).any(axis=1) )

ValueError: ('Lengths must match to compare', (1,), (7582, 2))

In [1041]:
team_a = fix_mi["blueTeamTag"].values[0]
team_b = fix_mi["redTeamTag"].values[0]
# Convert the two columns to a NumPy array
cols = matchinfo[['blueTeamTag', 'redTeamTag']].to_numpy()
mask = ( (cols == team_a).any(axis=1) ) & ( (cols == team_b).any(axis=1) )
filtered_df = matchinfo[mask]
wins=filtered_df.loc[:,['bResult','rResult']].sum()
d = {"WIN RATE BLUE":wins['bResult']/wins.sum()*100,"WIN RATE RED":wins['rResult']/wins.sum()*100}

In [1048]:
def get_team_scores(df, value_1, value_2):
    teams = [value_1, value_2]
    scores = {}
    for team in teams:
        blue_score = df.loc[df['blueTeamTag'] == team, 'bResult'].sum()
        red_score = df.loc[df['redTeamTag'] == team, 'rResult'].sum()
        total_score = blue_score + red_score
        scores[team] = total_score
    return scores

# Example usage:
scores = get_team_scores(filtered_df, team_a, team_b)
print(scores)

{'SKT': np.int64(37), 'KT': np.int64(16)}


In [1049]:
fix_mi

League  Year  Season    Type blueTeamTag  bResult  rResult redTeamTag  \
3333    LCK  2017  Summer  Season         SKT        1        0         KT   

      gamelength blueTop  ... blueBan1  redBan1 blueBan2     redBan2 blueBan3  \
3333          34  Untara  ...   Thresh  Chogath    Elise  Cassiopeia  Caitlyn   

     redBan3 blueBan4  redBan4   blueBan5  redBan5  
3333  Maokai    Rakan  Orianna  TahmKench  Taliyah  

[1 rows x 40 columns]

In [1076]:
plot_team_win_bar(team_a, team_b, fix_mi, scores)

In [ ]:
import plotly.graph_objects as go

def plot_team_win_bar(blue_team, red_team, row, scores):
    # Extract values
    blue_score = scores[blue_team]
    red_score = scores[red_team]
    total = blue_score + red_score

    # Compute win ratios
    blue_pct = blue_score / total * 100
    red_pct = red_score / total * 100

    # Determine winner
    if row['bResult'].values[0] > row['rResult'].values[0]: winner = blue_team  
    else: red_team

    # Define colors
    team_colors = {
        blue_team: {
            'low': f"rgba(0, 0, 255, 0.4)",     # light blue
            'full': f"rgba(0, 0, 255, 1.0)"      # strong blue
        },
        red_team: {
            'low': f"rgba(255, 0, 0, 0.4)",     # light red
            'full': f"rgba(255, 0, 0, 1.0)"      # strong red
        }
    }

    # Create base bars (win rate)
    fig = go.Figure()

    for team, pct in [(blue_team, blue_pct), (red_team, red_pct)]:
        fig.add_trace(go.Bar(
            x=[team],
            y=[pct],
            marker_color=team_colors[team]['low'],
            name=team,
            hovertemplate=f"{team} Win Rate: {pct:.1f}%",
            showlegend=False
        ))

        # Add full saturation bar only if this team won the current match
        if team == winner:
            fig.add_trace(go.Bar(
                x=[team],
                y=[2],  # a small height just to cap the top
                marker_color=team_colors[team]['full'],
                name=f"{team} (won)",
                hoverinfo="skip",
                showlegend=False
            ))

    # Layout
    fig.update_layout(
        barmode='stack',
        xaxis_title=None,
        yaxis_title=None,
        height=400,
        title="All Time Win Rates",
        margin=dict(t=40),
        yaxis_range=[0, 100],
    )

    return fig


In [1045]:
filtered_df.loc[filtered_df['redTeamTag'] == team_a, 'rResult']

2079    1
2147    0
2148    1
2281    1
2348    1
2349    1
2418    1
2511    1
2630    0
2674    1
2767    1
2864    1
2875    1
2876    1
2877    0
2878    0
3002    1
3004    1
3013    0
3127    1
3128    1
3129    1
3227    0
3229    1
3332    0
3351    0
3353    1
3354    1
3355    1
7501    0
7503    0
Name: rResult, dtype: int64

In [1044]:
filtered_df

League  Year  Season      Type blueTeamTag  bResult  rResult redTeamTag  \
2079    LCK  2015  Spring    Season          KT        0        1        SKT   
2080    LCK  2015  Spring    Season         SKT        1        0         KT   
2146    LCK  2015  Spring    Season         SKT        1        0         KT   
2147    LCK  2015  Spring    Season          KT        1        0        SKT   
2148    LCK  2015  Spring    Season          KT        0        1        SKT   
2281    LCK  2015  Summer    Season          KT        0        1        SKT   
2282    LCK  2015  Summer    Season         SKT        1        0         KT   
2347    LCK  2015  Summer    Season         SKT        0        1         KT   
2348    LCK  2015  Summer    Season          KT        0        1        SKT   
2349    LCK  2015  Summer    Season          KT        0        1        SKT   
2417    LCK  2015  Summer  Playoffs         SKT        1        0         KT   
2418    LCK  2015  Summer  Playoffs          KT        0        1        SKT   
2419    LCK  2015  Summer  Playoffs         SKT        1        0         KT   
2510    LCK  2016  Spring    Season         SKT        1        0         KT   
2511    LCK  2016  Spring    Season          KT        0        1        SKT   
2630    LCK  2016  Spring    Season          KT        1        0        SKT   
2631    LCK  2016  Spring    Season         SKT        0        1         KT   
2674    LCK  2016  Summer    Season          KT        0        1        SKT   
2675    LCK  2016  Summer    Season         SKT        1        0         KT   
2766    LCK  2016  Summer    Season         SKT        0        1         KT   
2767    LCK  2016  Summer    Season          KT        0        1        SKT   
2768    LCK  2016  Summer    Season         SKT        1        0         KT   
2863    LCK  2016  Spring  Playoffs         SKT        1        0         KT   
2864    LCK  2016  Spring  Playoffs          KT        0        1        SKT   
2865    LCK  2016  Spring  Playoffs         SKT        1        0         KT   
2875    LCK  2016  Summer  Playoffs          KT        0        1        SKT   
2876    LCK  2016  Summer  Playoffs          KT        0        1        SKT   
2877    LCK  2016  Summer  Playoffs          KT        1        0        SKT   
2878    LCK  2016  Summer  Playoffs          KT        1        0        SKT   
2879    LCK  2016  Summer  Playoffs         SKT        0        1         KT   
3002    LCK  2017  Spring    Season          KT        0        1        SKT   
3003    LCK  2017  Spring    Season         SKT        0        1         KT   
3004    LCK  2017  Spring    Season          KT        0        1        SKT   
3012    LCK  2017  Spring    Season         SKT        1        0         KT   
3013    LCK  2017  Spring    Season          KT        1        0        SKT   
3014    LCK  2017  Spring    Season         SKT        1        0         KT   
3127    LCK  2017  Spring  Playoffs          KT        0        1        SKT   
3128    LCK  2017  Spring  Playoffs          KT        0        1        SKT   
3129    LCK  2017  Spring  Playoffs          KT        0        1        SKT   
3227    LCK  2017  Summer    Season          KT        1        0        SKT   
3228    LCK  2017  Summer    Season         SKT        1        0         KT   
3229    LCK  2017  Summer    Season          KT        0        1        SKT   
3331    LCK  2017  Summer    Season         SKT        1        0         KT   
3332    LCK  2017  Summer    Season          KT        1        0        SKT   
3333    LCK  2017  Summer    Season         SKT        1        0         KT   
3351    LCK  2017  Summer  Playoffs          KT        1        0        SKT   
3352    LCK  2017  Summer  Playoffs         SKT        0        1         KT   
3353    LCK  2017  Summer  Playoffs          KT        0        1        SKT   
3354    LCK  2017  Summer  Playoffs          KT        0        1        SKT   
3355 

In [1020]:
wins=matchinfo.loc[:,['bResult','rResult']].sum()
d = {"WIN RATE BLUE":wins['bResult']/wins.sum()*100,"WIN RATE RED":wins['rResult']/wins.sum()*100}
fig = px.bar(
    x=d.keys(),
    y=d.values(),
    color=d.keys(),
    width=500,
    color_discrete_map=dict(zip(d.keys(), ('blue', 'red')))
)

fig.update_traces(
    width=0.75,
    hovertemplate="%{y:.1f}%",  # Custom hover text
)

fig.update_layout(
    showlegend=False,
    xaxis_title=None,
    yaxis_title=None
)
fig.show()

In [ ]:
config={'displayModeBar': False, 'staticPlot': True }

# Champion plots

In [ ]:
matchinfo

# Gantt chart

In [ ]:
import plotly.express as px
import pandas as pd

import plotly.express as px
import pandas as pd
import plotly.graph_objects as go

# Your data
df = pd.DataFrame([
    dict(Task="Project", Start='2025-04-24', Finish='2025-05-22'),
    dict(Task="Create base Dash structure", Start='2025-04-25', Finish='2025-05-02'),
    dict(Task="Create all base visualisations", Start='2025-04-25', Finish='2025-05-05'),
    dict(Task="Link visualisations with Dash", Start='2025-05-02', Finish='2025-05-06'),
    dict(Task="Implement filters & interconnectivity", Start='2025-05-05', Finish='2025-05-12'),
    dict(Task="(OPTIONAL) Expand dataset", Start='2025-05-05', Finish='2025-05-19'),
    dict(Task="Apply Final polish", Start='2025-05-12', Finish='2025-05-19'),
    dict(Task="Validate & Evaluate", Start='2025-05-14', Finish='2025-05-21'),
    dict(Task="Prepare Final presentation", Start='2025-05-19', Finish='2025-05-22'),
    dict(Task="Prepare Deliverables & Write Report", Start='2025-05-22', Finish='2025-05-25'),
])

# Define custom colors
colors = {
    task: "#3d7094" if "(OPTIONAL)" in task else "#1f77b4"  # less saturated for optional
    for task in df["Task"]
}

# Create the Gantt chart
fig = px.timeline(df, x_start="Start", x_end="Finish", y="Task", color="Task", color_discrete_map=colors)
fig.update_layout(showlegend=False)
fig.update_yaxes(autorange="reversed")

# Add dotted vertical lines for each day
start_date = pd.to_datetime(df["Start"].min())
end_date = pd.to_datetime(df["Finish"].max())

for d in pd.date_range(start=start_date, end=end_date):
    fig.add_vline(
        x=d,
        line=dict(color='rgba(60, 60, 60, 0.5)', width=1, dash="dot"),
        layer="above"
    )

# Add red lines
highlight_lines = [
    ('2025-04-24', 'dot', "Progress<br>Presentation"),  # dotted red
    ('2025-05-22', 'solid', 'Final<br>Presentation'),  # solid red
    ('2025-05-25', 'solid', 'Deliverables')   # solid red
]

for date_str, dash, label in highlight_lines:
    # Red vertical line
    fig.add_vline(
        x=date_str,
        line=dict(color='red', width=2, dash=dash)
    )
    # Annotation below chart
    fig.add_annotation(
        x=date_str,
        y=1.02,  # slightly below visible chart
        xref='x',
        yref='paper',
        text=label,
        showarrow=False,
        yanchor='bottom',
        xanchor='center',
        font=dict(color='red', size=12)
    )

fig.update_layout(
    title="Gantt Chart of future progress",
    margin=dict(t=100)  # Extra space at bottom for annotations
)

fig.show()
